In [1]:
import sys
sys.path.append("../src") 
from dolfin import *
import meshio
import pyvista as pv
import numpy as np
from utils import *
from materials import *
import fea_transient
import LB_transient
import max_omega 

In [2]:
mesh_file = "../mesh/disk.inp" # .inp or .xdmf
comp_list1 = np.linspace(1.,1.,101)
comp_list2 = np.linspace(1.,0.,22)[1:-1]
comp_list3 = np.linspace(0.,0.,15)
comp_list = np.concatenate((comp_list1,comp_list2,comp_list3))

mesh = read_mesh(mesh_file)
properties = get_properties(mesh,comp_list)
Displacement_BC = 'fix-free' # fix-free or free-free

t_rise = 1. # time to heat to the max temp.
t_heatdwell = 20. # heating dwell time
t_fall = 3. # time to cool to the ambient temp
t_cooldwell = 600. # cooling dwell time

In [3]:
def run_fea_wrap(omega,T_load):
    n_cyc = 15 # number of simulated cycles

    time_step = 1. # time step size
    time_step_coarse = 20. # use a coarser time step at during cooling dwell
    plastic_inverval = 1 # elasto-plastic simulation every N thermal time step
    
    load = get_loadfunc(T_load,t_rise,t_heatdwell,t_fall,t_cooldwell)

    t_cycle = t_rise + t_heatdwell + t_fall + t_cooldwell
    t_fine = t_rise + t_heatdwell + t_fall*2.
    t_list = get_time_list(t_cycle,t_fine,time_step,time_step_coarse,n_cyc)
    
    results = fea_transient.run_simulation(mesh,properties,load,omega,t_list,Displacement_BC,plastic_inverval)
    PEEQ = results[:,1]
    period = (len(PEEQ)-1)/n_cyc
    assert period-int(period) == 0
    SD_flag = fea_transient.check_PEEQ(PEEQ,int(period),tol=1e-8)
    return SD_flag

In [11]:
def run_lb_wrap(omega,T_load):
    time_step = 1. # time step size
    time_step_coarse = 10. # use a coarser time step at during cooling dwell
    plastic_inverval = 1 # elasto-plastic simulation every N thermal time step
    
    sd_flag = LB_transient.run(mesh,properties,T_load,omega,t_rise,t_heatdwell,t_fall,t_cooldwell,
                 Displacement_BC,time_step,time_step_coarse)
    
    if sd_flag.max()>1.001:
        print('Not Shakedown!')
        SD_flag = 0
    else:
        print('Shakedown!')
        SD_flag = 1
    return SD_flag

In [5]:
%%time
run_fea_wrap(1000,1000)

/home/bizon/anaconda3/envs/fenicsproject/lib/python3.11/site-packages/ffc/jitcompiler.py:234: QuadratureRepresentationDeprecationWarning: 
*** ===================================================== ***
*** FFC: quadrature representation is deprecated! It will ***
*** likely be removed in 2018.2.0 release. Use uflacs     ***
*** representation instead.                               ***
*** ===================================================== ***
  issue_deprecation_warning()


Solving linear variational problem.
Residual0: 516018.80302469124
Residual: 28231.55605834689
Residual: 78.66311826227582
Residual: 0.010000995143348576
Solving linear variational problem.
Residual0: 208886.82334093974
Residual: 9634.82226143824
Residual: 44.475896928602445
Residual: 0.003369833542733134
Solving linear variational problem.
Residual0: 150601.21665223723
Residual: 4547.381551559485
Residual: 19.392269742645237
Residual: 0.0009610684286195676
Solving linear variational problem.
Residual0: 119089.8508023303
Residual: 729.497301915588
Residual: 0.6004178407087712
Solving linear variational problem.
Residual0: 99256.5908633686
Residual: 87.37370190598962
Residual: 0.007930592250849097
Solving linear variational problem.
Residual0: 85655.71686029405
Residual: 1573.0458278972071
Residual: 1.5863626157209645
Residual: 3.3042484490355605e-06
Solving linear variational problem.
Residual0: 75773.0663572057
Residual: 24.153246478530015
Residual: 0.0008725547713831355
Solving linear

Residual: 7.482509497521489e-10
Solving linear variational problem.
Residual0: 40339.76060499976
Residual: 6.67087124418703e-10
Solving linear variational problem.
Residual0: 38962.42819855659
Residual: 6.227837414494784e-10
Solving linear variational problem.
Residual0: 37728.027489604814
Residual: 5.496043663143757e-10
Solving linear variational problem.
Residual0: 36614.26695157189
Residual: 5.127461357028734e-10
Solving linear variational problem.
Residual0: 35603.1380806162
Residual: 5.875122123160892e-10
Solving linear variational problem.
Residual0: 171692.0128029121
Residual: 4.766053800542739e-10
Solving linear variational problem.
Residual0: 217400.90945709258
Residual: 1.0349885932068978e-09
Solving linear variational problem.
Residual0: 251872.87585462132
Residual: 7200.036877485293
Residual: 43.65981166572444
Residual: 0.0052354840651776344
Solving linear variational problem.
Residual0: 147425.69453868383
Residual: 407.03763349392204
Residual: 0.43936766601110955
Solving l

Solving linear variational problem.
Residual0: 6768.859220700161
Residual: 1.9243287813056585e-10
Solving linear variational problem.
Residual0: 6351.514787881221
Residual: 1.8428827179512375e-10
Solving linear variational problem.
Residual0: 5980.016516076193
Residual: 1.7302467415407093e-10
Solving linear variational problem.
Residual0: 5646.589833442882
Residual: 1.833337033486403e-10
Solving linear variational problem.
Residual0: 5344.996346663256
Residual: 1.608978830965259e-10
Solving linear variational problem.
Residual0: 5070.22089456691
Residual: 1.7044851071627988e-10
Solving linear variational problem.
Residual0: 4818.222039793653
Residual: 1.6865441820701832e-10
Solving linear variational problem.
Residual0: 4585.73302669344
Residual: 1.671962316188544e-10
Solving linear variational problem.
Residual0: 4370.103195401786
Residual: 1.4718286127627917e-10
Solving linear variational problem.
Residual0: 4169.171887848212
Residual: 1.459101697213622e-10
Solving linear variational

Residual: 6.41343873527506e-10
Solving linear variational problem.
Residual0: 36601.33026696654
Residual: 6.479716473115049e-10
Solving linear variational problem.
Residual0: 35589.58687619094
Residual: 5.94745138302513e-10
Solving linear variational problem.
Residual0: 171689.60318581833
Residual: 6.166015006361641e-10
Solving linear variational problem.
Residual0: 217399.39672974317
Residual: 8.180697067522815e-10
Solving linear variational problem.
Residual0: 251871.9265984208
Residual: 7050.459401420186
Residual: 41.34245620205734
Residual: 0.0045399504913114334
Solving linear variational problem.
Residual0: 147424.18247751112
Residual: 390.41823394893345
Residual: 0.42888610189520227
Solving linear variational problem.
Residual0: 111329.04853244756
Residual: 173.91611890339024
Residual: 0.002650122848596233
Solving linear variational problem.
Residual0: 89149.95784881995
Residual: 4.817538578150617
Residual: 4.398848573785182e-05
Solving linear variational problem.
Residual0: 4885

...

Residual0: 75752.96954634329
Residual: 9.473709956291885e-10
Solving linear variational problem.
Residual0: 68263.34923393972
Residual: 8.980883957100555e-10
Solving linear variational problem.
Residual0: 62406.24869827721
Residual: 8.806527479251766e-10
Solving linear variational problem.
Residual0: 57709.39831369059
Residual: 7.741986172623799e-10
Solving linear variational problem.
Residual0: 53864.6967603408
Residual: 6.965825038716395e-10
Solving linear variational problem.
Residual0: 50662.68171345231
Residual: 6.508458744913777e-10
Solving linear variational problem.
Residual0: 47956.171785083214
Residual: 6.693728157701443e-10
Solving linear variational problem.
Residual0: 45638.89694896557
Residual: 6.48216307233275e-10
Solving linear variational problem.
Residual0: 43632.3418017282
Residual: 6.528752029756091e-10
Solving linear variational problem.
Residual0: 41877.33432980448
Residual: 6.96357763391824e-10
Solving linear variational problem.
Residual0: 40328.49881658204
Resi

Residual: 1.070947119076216e-09
Solving linear variational problem.
Residual0: 77787.8499442359
Residual: 1.023851457783859e-09
Solving linear variational problem.
Residual0: 56569.30349996806
Residual: 7.915574901493463e-10
Solving linear variational problem.
Residual0: 43555.1185272877
Residual: 6.069526091753267e-10
Solving linear variational problem.
Residual0: 34826.68696815772
Residual: 5.937138162713587e-10
Solving linear variational problem.
Residual0: 28618.586787211385
Residual: 5.369268479137529e-10
Solving linear variational problem.
Residual0: 24018.002444629066
Residual: 4.495925035888701e-10
Solving linear variational problem.
Residual0: 20503.058449407483
Residual: 4.018644660151729e-10
Solving linear variational problem.
Residual0: 17753.313656617127
Residual: 3.818870895214065e-10
Solving linear variational problem.
Residual0: 15561.333463826246
Residual: 3.4697970858512144e-10
Solving linear variational problem.
Residual0: 13787.047377546918
Residual: 2.8952384307495

Residual: 1.395978151068074e-10
Solving linear variational problem.
Residual0: 516057.6146582965
Residual: 6948.580445705275
Residual: 44.13865764657859
Residual: 0.005380532991895875
Solving linear variational problem.
Residual0: 208880.49781271938
Residual: 1370.452181725684
Residual: 4.018686387784348
Residual: 5.9744832838924706e-05
Solving linear variational problem.
Residual0: 150592.024406762
Residual: 517.2386635669772
Residual: 0.2418019098806459
Solving linear variational problem.
Residual0: 119077.94424621947
Residual: 61.72125871319015
Residual: 0.001099499627503255
Solving linear variational problem.
Residual0: 99242.05330113471
Residual: 64.50809886155082
Residual: 0.00043106931820425197
Solving linear variational problem.
Residual0: 85638.39662032896
Residual: 30.215370682878895
Residual: 2.457412788509998e-10
Solving linear variational problem.
Residual0: 75752.96950119779
Residual: 1.0144946671280173e-09
Solving linear variational problem.
Residual0: 68263.34918220899


Residual: 6987.083966527205
Residual: 40.13689659958813
Residual: 0.004220039396065709
Solving linear variational problem.
Residual0: 147424.14898464968
Residual: 382.34027052242595
Residual: 0.4312907259500643
Solving linear variational problem.
Residual0: 111329.00505102734
Residual: 168.6502210925058
Residual: 0.0026883770370682916
Solving linear variational problem.
Residual0: 89149.9037374518
Residual: 4.777065338830324
Residual: 4.247580177468368e-05
Solving linear variational problem.
Residual0: 488516.0851063679
Residual: 893.7073433302708
Residual: 9.883779089143274e-10
Solving linear variational problem.
Residual0: 208952.0508428561
Residual: 2.1276834927488145e-09
Solving linear variational problem.
Residual0: 117537.55896545992
Residual: 1.3229138169631834e-09
Solving linear variational problem.
Residual0: 77787.85022204818
Residual: 1.0119210523273619e-09
Solving linear variational problem.
Residual0: 56569.30402376967
Residual: 7.453548033027584e-10
Solving linear variati

0

In [6]:
%%time
run_lb_wrap(1000,1000)

Simulation time: 1.0
Solving linear variational problem.
    Residual0: 516018.80302469124
    Residual: 28231.556058346883
    Residual: 78.66311826296669
    Residual: 0.01000099489505065
Simulation time: 2.0
Solving linear variational problem.
    Residual0: 208886.8233409398
    Residual: 9634.822261438598
    Residual: 44.47589692857633
    Residual: 0.003369833527017674
Simulation time: 3.0
Solving linear variational problem.
    Residual0: 150601.2166522372
    Residual: 4547.381551559278
    Residual: 19.392269742648683
    Residual: 0.0009610684163818216
Simulation time: 4.0
Solving linear variational problem.
    Residual0: 119089.85080233027
    Residual: 729.4973019156171
    Residual: 0.6004178407436217
Simulation time: 5.0
Solving linear variational problem.
    Residual0: 99256.59086336862
    Residual: 87.37370190570046
    Residual: 0.007930592260130603
Simulation time: 6.0
Solving linear variational problem.
    Residual0: 85655.71686029407
    Residual: 1573.04582789

Simulation time: 357.0
Solving linear variational problem.
    Residual0: 3758.286881049268
    Residual: 1.0371042521981984e-10
Simulation time: 367.0
Solving linear variational problem.
    Residual0: 3575.8252761094145
    Residual: 9.84604138052097e-11
Simulation time: 377.0
Solving linear variational problem.
    Residual0: 3408.586386913632
    Residual: 1.068119660819319e-10
Simulation time: 387.0
Solving linear variational problem.
    Residual0: 3255.019314402043
    Residual: 1.0598808205361523e-10
Simulation time: 397.0
Solving linear variational problem.
    Residual0: 3113.7389333104943
    Residual: 1.0475053072771827e-10
Simulation time: 407.0
Solving linear variational problem.
    Residual0: 2983.506506787662
    Residual: 1.026675663197934e-10
Simulation time: 417.0
Solving linear variational problem.
    Residual0: 2863.2132439776333
    Residual: 9.862088048889087e-11
Simulation time: 427.0
Solving linear variational problem.
    Residual0: 2751.8661857530437
    Re

0

In [7]:
omega_max = max_omega.run(mesh,properties,Displacement_BC)

Trying Omega =  1000
Residual =  714.9072173832941
Residual =  3.848212357446955e-09
Trying Omega =  2000
Residual =  2144.7216521497107
Residual =  1.1391760044184608e-08
Trying Omega =  3000
Residual =  3574.536086916992
Residual =  67.65578744955592
Residual =  6.0379490166080645
Residual =  0.006236093680099123
Residual =  2.2409024862817036e-08
Trying Omega =  4000
Residual =  5004.350521683075
Residual =  66504.97193093292
Residual =  77304.02548210656
Residual =  85924.20348685692
Residual =  384063.7100309081
Residual =  16975.23668560753
Residual =  2960.79685284771
Residual =  80.13096004083569
Residual =  0.057937105739311406
Residual =  3.082210133967915e-06
Trying Omega =  3500.0
Residual =  2323.448456495723
Residual =  3757.1524943728946
Residual =  369.4374070517939
Residual =  58.67958717054048
Residual =  1.6138194903872867
Residual =  0.000123129548733437
Trying Omega =  4000.0
Residual =  2680.902065308624
Residual =  80663.00764915411
Residual =  79092.74358959505


In [8]:
num_om = 5
omega_list = (np.arange(1,num_om)/num_om*omega_max**2)**0.5
omega_list

array([1749.54849958, 2474.23521614, 3030.30689158, 3499.09699917])

In [9]:
T_tol = 10
T_SD_list_fea = []
for omega in omega_list:
    T_min = 0.
    T_max = 2000.
    while (T_max-T_min)>T_tol:
        T_load = (T_max+T_min)/2.
        flag = run_fea_wrap(omega,T_load)
        if flag == 1:
            T_min = T_load
        else:
            T_max = T_load
    T_SD_list_fea.append((T_max+T_min)/2.)
T_SD_list_fea

Solving linear variational problem.
Residual0: 515937.55753630964
Residual: 26052.327819927348
Residual: 81.79712983339462
Residual: 0.012076103534573415
Residual0: 208886.82332835472
Solving linear variational problem.
Residual: 7239.092418462626
Residual: 36.84976498899701
Residual: 0.0025004521829509346
Solving linear variational problem.
Residual0: 150601.21664201585
Residual: 2683.608660239319
Residual: 9.34207347279383
Residual: 0.0002728682265843426
Solving linear variational problem.
Residual0: 119089.85080709365
Residual: 2486.679808875188
Residual: 5.137164920935504
Residual: 3.704163316472821e-05
Solving linear variational problem.
Residual0: 99256.64924520015
Residual: 1374.8752931421595
Residual: 1.6869873868500123
Residual: 8.09283097097223e-06
Solving linear variational problem.
Residual0: 85655.71655165013
Residual: 34.321639180068146
Residual: 0.0010131170134526845
Solving linear variational problem.
Residual0: 75773.06641121561
Residual: 1105.2525938895542
Residual: 0

Residual: 5.005760258978472e-10
Solving linear variational problem.
Residual0: 38962.4281985566
Residual: 5.168752442568573e-10
Solving linear variational problem.
Residual0: 37728.02748960482
Residual: 6.673226052696972e-10
Solving linear variational problem.
Residual0: 36614.26695157189
Residual: 5.609389097119169e-10
Solving linear variational problem.
Residual0: 35603.138080616205
Residual: 5.686144801435378e-10
Solving linear variational problem.
Residual0: 171692.012802912
Residual: 6.6610084270999e-10
Solving linear variational problem.
Residual0: 217400.9094570925
Residual: 1.0024001359708657e-09
Solving linear variational problem.
Residual0: 251872.87585462176
Residual: 7177.996814936073
Residual: 43.21273407644217
Residual: 0.005093017522203053
Solving linear variational problem.
Residual0: 147425.69454137242
Residual: 403.455580235689
Residual: 0.43780134165500123
Solving linear variational problem.
Residual0: 111331.02075977031
Residual: 183.08949061682983
Residual: 0.00261

Residual: 2.4734129813420624e-10
Solving linear variational problem.
Residual0: 9131.32770654794
Residual: 2.3937272687078084e-10
Solving linear variational problem.
Residual0: 8405.814550440638
Residual: 2.210525376526505e-10
Solving linear variational problem.
Residual0: 7782.33603854574
Residual: 2.4334158834686565e-10
Solving linear variational problem.
Residual0: 7241.754556064575
Residual: 1.8722207275601788e-10
Solving linear variational problem.
Residual0: 6768.859220700162
Residual: 1.800135071794315e-10
Solving linear variational problem.
Residual0: 6351.514787881223
Residual: 1.973995856388161e-10
Solving linear variational problem.
Residual0: 5980.016516076208
Residual: 1.857930321138961e-10
Solving linear variational problem.
Residual0: 5646.589833442874
Residual: 1.8483666342802127e-10
Solving linear variational problem.
Residual0: 5344.996346663258
Residual: 1.7176750656170613e-10
Solving linear variational problem.
Residual0: 5070.220894566905
Residual: 1.68089896269601

Residual: 8.690825875950809e-10
Solving linear variational problem.
Residual0: 68263.45982559399
Residual: 8.925565333367484e-10
Solving linear variational problem.
Residual0: 62406.37371064596
Residual: 7.541627603306299e-10
Solving linear variational problem.
Residual0: 57709.53802646458
Residual: 7.705219782484468e-10
Solving linear variational problem.
Residual0: 53864.851379458596
Residual: 6.557875966432703e-10
Solving linear variational problem.
Residual0: 50662.851369089745
Residual: 7.384251107449161e-10
Solving linear variational problem.
Residual0: 47956.356534200095
Residual: 6.97182171229133e-10
Solving linear variational problem.
Residual0: 45639.09678041698
Residual: 6.946578992461118e-10
Solving linear variational problem.
Residual0: 43632.55664278396
Residual: 6.815623080437295e-10
Solving linear variational problem.
Residual0: 41877.56405336212
Residual: 6.389734373512601e-10
Solving linear variational problem.
Residual0: 40328.74324859901
Residual: 6.16446785486001e-

Residual: 5.738950428649941e-10
Solving linear variational problem.
Residual0: 34824.75395815788
Residual: 5.519360767255795e-10
Solving linear variational problem.
Residual0: 28616.36148267389
Residual: 4.6076421670284774e-10
Solving linear variational problem.
Residual0: 24015.548025963173
Residual: 3.789059320158866e-10
Solving linear variational problem.
Residual0: 20500.428466746886
Residual: 4.5560248267248815e-10
Solving linear variational problem.
Residual0: 17750.553409198204
Residual: 3.605485704871242e-10
Solving linear variational problem.
Residual0: 15558.481395204797
Residual: 3.602400674236083e-10
Solving linear variational problem.
Residual0: 13784.136276527672
Residual: 2.907646479611869e-10
Solving linear variational problem.
Residual0: 12329.468593488642
Residual: 2.6946482774413917e-10
Solving linear variational problem.
Residual0: 11123.657549720694
Residual: 3.132507886276088e-10
Solving linear variational problem.
Residual0: 10114.147442577709
Residual: 2.4631450

...

Residual: 9.923216669613451e-11
Solving linear variational problem.
Residual0: 1438.8396417468634
Residual: 9.378710816576823e-11
Solving linear variational problem.
Residual0: 1345.8374418387532
Residual: 9.304073016426294e-11
Solving linear variational problem.
Residual0: 1263.6405498981924
Residual: 9.349507770018761e-11
Solving linear variational problem.
Residual0: 1190.368323217782
Residual: 8.888090809345927e-11
Solving linear variational problem.
Residual0: 1124.514647886316
Residual: 9.035679445074998e-11
Solving linear variational problem.
Residual0: 1064.8711575305426
Residual: 8.646740630406867e-11
Solving linear variational problem.
Residual0: 1010.4663488975748
Residual: 7.889087895341563e-11
Solving linear variational problem.
Residual0: 960.5171216447571
Residual: 9.556937241641741e-11
Solving linear variational problem.
Residual0: 914.3901806228266
Residual: 8.96948767011332e-11
Solving linear variational problem.
Residual0: 871.5713255945361
Residual: 9.51419379507262

Residual: 1.0346988885689328e-10
Solving linear variational problem.
Residual0: 42460.813119779355
Residual: 2.238709608464488e-10
Solving linear variational problem.
Residual0: 49193.73155584953
Residual: 2.8740043956516786e-10
Solving linear variational problem.
Residual0: 28793.779113939803
Residual: 2.1727290633019954e-10
Solving linear variational problem.
Residual0: 21743.947054101147
Residual: 1.513511892821154e-10
Solving linear variational problem.
Residual0: 17412.09057730049
Residual: 1.1726490897720293e-10
Solving linear variational problem.
Residual0: 95413.2979216242
Residual: 7.120749682705663e-10
Solving linear variational problem.
Residual0: 40810.947468145954
Residual: 3.444801070295079e-10
Solving linear variational problem.
Residual0: 22956.554482174084
Residual: 2.3776799012598197e-10
Solving linear variational problem.
Residual0: 15192.939442233554
Residual: 2.129267685359329e-10
Solving linear variational problem.
Residual0: 11048.692089837486
Residual: 1.4965724

Solving linear variational problem.
Residual0: 914.3926316228359
Residual: 9.440657764019312e-11
Solving linear variational problem.
Residual0: 871.5736844491781
Residual: 9.54846903176643e-11
Solving linear variational problem.
Residual0: 831.6433299483765
Residual: 9.432472931376487e-11
Solving linear variational problem.
Residual0: 100792.50286294853
Residual: 8.606919823436592e-10
Solving linear variational problem.
Residual0: 40796.97225736424
Residual: 3.1289875043806057e-10
Solving linear variational problem.
Residual0: 29412.504767001592
Residual: 2.333379698723016e-10
Solving linear variational problem.
Residual0: 23257.411384804684
Residual: 2.090012868781014e-10
Solving linear variational problem.
Residual0: 19383.21353603965
Residual: 2.1171369928318433e-10
Solving linear variational problem.
Residual0: 16726.24933991343
Residual: 1.9488533585328957e-10
Solving linear variational problem.
Residual0: 14795.501855702681
Residual: 1.496293567187036e-10
Solving linear variation

Solving linear variational problem.
Residual0: 95413.29787233447
Residual: 6.721718408833059e-10
Solving linear variational problem.
Residual0: 40810.947430245295
Residual: 4.261082561898209e-10
Solving linear variational problem.
Residual0: 22956.55448544137
Residual: 2.572445664348676e-10
Solving linear variational problem.
Residual0: 15192.939496493756
Residual: 1.9447758134516893e-10
Solving linear variational problem.
Residual0: 11048.692192142495
Residual: 1.6182752005068763e-10
Solving linear variational problem.
Residual0: 8506.859230576734
Residual: 1.3013687766658135e-10
Solving linear variational problem.
Residual0: 6802.087475111626
Residual: 1.2693835100624073e-10
Solving linear variational problem.
Residual0: 5589.567935231754
Residual: 1.2225988463813172e-10
Solving linear variational problem.
Residual0: 4691.016326751618
Residual: 1.13442504979983e-10
Solving linear variational problem.
Residual0: 4004.503843726639
Residual: 1.0848741606025704e-10
Solving linear variati

[886.71875, 886.71875, 74.21875, 191.40625]

In [12]:
%%time
T_tol = 10
T_SD_list_sd = []
for omega in omega_list:
    T_min = 0.
    T_max = 2000.
    while (T_max-T_min)>T_tol:
        T_load = (T_max+T_min)/2.
        flag = run_lb_wrap(omega,T_load)
        if flag == 1:
            T_min = T_load
        else:
            T_max = T_load
    T_SD_list_sd.append((T_max+T_min)/2.)
T_SD_list_sd

Simulation time: 1.0
Solving linear variational problem.
    Residual0: 515937.55753630964
    Residual: 26052.327819927363
    Residual: 81.79712983340045
    Residual: 0.01207610344503348
Simulation time: 2.0
Solving linear variational problem.
    Residual0: 208886.8233283547
    Residual: 7239.092418462346
    Residual: 36.849764989053384
    Residual: 0.0025004520125431373
Simulation time: 3.0
Solving linear variational problem.
    Residual0: 150601.21664201582
    Residual: 2683.608660239523
    Residual: 9.342073472824968
    Residual: 0.0002728682095001132
Simulation time: 4.0
Solving linear variational problem.
    Residual0: 119089.85080709365
    Residual: 2486.67980887533
    Residual: 5.137164920976292
    Residual: 3.704163057768276e-05
Simulation time: 5.0
Solving linear variational problem.
    Residual0: 99256.64924520015
    Residual: 1374.875293142017
    Residual: 1.6869873868575487
    Residual: 8.092853842586195e-06
Simulation time: 6.0
Solving linear variational

    Residual: 1.1158673675292183e-10
Simulation time: 357.0
Solving linear variational problem.
    Residual0: 3758.286881049271
    Residual: 1.2801740967922234e-10
Simulation time: 367.0
Solving linear variational problem.
    Residual0: 3575.8252761094163
    Residual: 1.0921246320199335e-10
Simulation time: 377.0
Solving linear variational problem.
    Residual0: 3408.5863869136338
    Residual: 1.0315564699053405e-10
Simulation time: 387.0
Solving linear variational problem.
    Residual0: 3255.0193144020545
    Residual: 1.0273393416987607e-10
Simulation time: 397.0
Solving linear variational problem.
    Residual0: 3113.738933310491
    Residual: 1.1239735095631633e-10
Simulation time: 407.0
Solving linear variational problem.
    Residual0: 2983.5065067876735
    Residual: 1.0459812569809944e-10
Simulation time: 417.0
Solving linear variational problem.
    Residual0: 2863.21324397763
    Residual: 9.501521061547678e-11
Simulation time: 427.0
Solving linear variational problem.

    Residual: 4.2575188697205785e-10
Simulation time: 7.0
Solving linear variational problem.
    Residual0: 37886.53317827476
    Residual: 3.91435428272478e-10
Simulation time: 8.0
Solving linear variational problem.
    Residual0: 34143.138903756095
    Residual: 4.0112450884249214e-10
Simulation time: 9.0
Solving linear variational problem.
    Residual0: 31216.02798840465
    Residual: 4.1033112599761887e-10
Simulation time: 10.0
Solving linear variational problem.
    Residual0: 28869.059320764656
    Residual: 4.1349868461933143e-10
Simulation time: 11.0
Solving linear variational problem.
    Residual0: 26948.175057767246
    Residual: 3.213388845650244e-10
Simulation time: 12.0
Solving linear variational problem.
    Residual0: 25348.63677441297
    Residual: 3.10735442955754e-10
Simulation time: 13.0
Solving linear variational problem.
    Residual0: 23996.84687110533
    Residual: 3.419352733704631e-10
Simulation time: 14.0
Solving linear variational problem.
    Residual0: 

    Residual: 7.53688965768729e-11
Simulation time: 537.0
Solving linear variational problem.
    Residual0: 959.3994140418309
    Residual: 8.088562018143423e-11
Simulation time: 547.0
Solving linear variational problem.
    Residual0: 933.1445715643329
    Residual: 6.283557247844353e-11
Simulation time: 557.0
Solving linear variational problem.
    Residual0: 908.1338947112389
    Residual: 6.653064255148997e-11
Simulation time: 567.0
Solving linear variational problem.
    Residual0: 884.2636218617008
    Residual: 6.778217889694575e-11
Simulation time: 577.0
Solving linear variational problem.
    Residual0: 861.4409689388025
    Residual: 7.07198166550931e-11
Simulation time: 587.0
Solving linear variational problem.
    Residual0: 839.582915111447
    Residual: 6.480848927114305e-11
Simulation time: 597.0
Solving linear variational problem.
    Residual0: 818.6151172800975
    Residual: 7.384937907631878e-11
Simulation time: 607.0
Solving linear variational problem.
    Residual

    Residual: 1.733466828024033e-10
Simulation time: 23.0
Solving linear variational problem.
    Residual0: 163054.40736513992
    Residual: 7.568898841609113e-10
Simulation time: 24.0
Solving linear variational problem.
    Residual0: 188906.9347173847
    Residual: 1.0064993232535235e-09
Simulation time: 25.0
Solving linear variational problem.
    Residual0: 110572.86285929728
    Residual: 6.856182449974986e-10
Simulation time: 26.0
Solving linear variational problem.
    Residual0: 83502.93116485226
    Residual: 7.572135258243558e-10
Simulation time: 27.0
Solving linear variational problem.
    Residual0: 66870.04950136409
    Residual: 5.404748027829097e-10
Simulation time: 37.0
Solving linear variational problem.
    Residual0: 270716.9364538887
    Residual: 2.1749062761671042e-09
Simulation time: 47.0
Solving linear variational problem.
    Residual0: 144384.52377508493
    Residual: 1.1056233273810514e-09
Simulation time: 57.0
Solving linear variational problem.
    Residua

...

0.9994566718254642
Simulation time: 15.0
Solving linear variational problem.
Solving linear variational problem.
0.9996193698903995
Simulation time: 16.0
Solving linear variational problem.
Solving linear variational problem.
0.9997783426961689
Simulation time: 17.0
Solving linear variational problem.
Solving linear variational problem.
0.9999389063230847
Simulation time: 18.0
Solving linear variational problem.
Solving linear variational problem.
1.0000976364573728
Simulation time: 19.0
Solving linear variational problem.
Solving linear variational problem.
1.0002535257562415
Simulation time: 20.0
Solving linear variational problem.
Solving linear variational problem.
1.000411247847028
Simulation time: 21.0
Solving linear variational problem.
Solving linear variational problem.
1.0005733243235688
Simulation time: 22.0
Solving linear variational problem.
Solving linear variational problem.
1.0003609289819875
Simulation time: 23.0
Solving linear variational problem.
Solving linear varia

    Residual: 8.408839012062386e-11
Simulation time: 267.0
Solving linear variational problem.
    Residual0: 303.01782084464367
    Residual: 8.77885717289692e-11
Simulation time: 277.0
Solving linear variational problem.
    Residual0: 282.6970968665391
    Residual: 9.16341941895955e-11
Simulation time: 287.0
Solving linear variational problem.
    Residual0: 264.3875604325909
    Residual: 9.03604893936402e-11
Simulation time: 297.0
Solving linear variational problem.
    Residual0: 247.85111516641172
    Residual: 9.534712652549993e-11
Simulation time: 307.0
Solving linear variational problem.
    Residual0: 232.88397339512656
    Residual: 9.700799643505053e-11
Simulation time: 317.0
Solving linear variational problem.
    Residual0: 219.31038058590863
    Residual: 9.509415219591253e-11
Simulation time: 327.0
Solving linear variational problem.
    Residual0: 206.9777006600295
    Residual: 8.76850985584894e-11
Simulation time: 337.0
Solving linear variational problem.
    Resid

    Residual: 406.0558438376686
    Residual: 53.89522171574974
    Residual: 0.30272963773453304
    Residual: 3.2011448839869415e-05
Simulation time: 2.0
Solving linear variational problem.
    Residual0: 11423.498131918092
    Residual: 0.5055887476688959
    Residual: 2.6911845581856776e-05
Simulation time: 3.0
Solving linear variational problem.
    Residual0: 8236.004028745214
    Residual: 4.7306039585980395
    Residual: 3.532859572445743e-05
Simulation time: 4.0
Solving linear variational problem.
    Residual0: 6512.726216597471
    Residual: 13.684577159289763
    Residual: 0.0005711671545762993
Simulation time: 5.0
Solving linear variational problem.
    Residual0: 5428.098005289751
    Residual: 0.0018764731488138573
Simulation time: 6.0
Solving linear variational problem.
    Residual0: 4684.296998960179
    Residual: 0.0015509469540191765
Simulation time: 7.0
Solving linear variational problem.
    Residual0: 4143.839566374085
    Residual: 8.70887017670367
    Residual:

    Residual: 9.521376415707985e-11
Simulation time: 417.0
Solving linear variational problem.
    Residual0: 156.58197428003027
    Residual: 9.287328202554267e-11
Simulation time: 427.0
Solving linear variational problem.
    Residual0: 150.49268203337206
    Residual: 8.851024683728126e-11
Simulation time: 437.0
Solving linear variational problem.
    Residual0: 144.84399726412698
    Residual: 7.907669130615144e-11
Simulation time: 447.0
Solving linear variational problem.
    Residual0: 139.59235829972943
    Residual: 8.931698206363079e-11
Simulation time: 457.0
Solving linear variational problem.
    Residual0: 134.69875941172933
    Residual: 9.01708842165332e-11
Simulation time: 467.0
Solving linear variational problem.
    Residual0: 130.12828667051642
    Residual: 8.74349447045991e-11
Simulation time: 477.0
Solving linear variational problem.
    Residual0: 125.84970165419068
    Residual: 8.711665884505785e-11
Simulation time: 487.0
Solving linear variational problem.
    

[878.90625, 878.90625, 58.59375, 58.59375]